<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Fake-news-detection" data-toc-modified-id="Fake-news-detection-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Fake news detection</a></span><ul class="toc-item"><li><span><a href="#Feature-extraction-functions" data-toc-modified-id="Feature-extraction-functions-1.1"><span class="toc-item-num">1.1&nbsp;&nbsp;</span>Feature extraction functions</a></span></li><li><span><a href="#Reading-and-preparing-the-corpus" data-toc-modified-id="Reading-and-preparing-the-corpus-1.2"><span class="toc-item-num">1.2&nbsp;&nbsp;</span>Reading and preparing the corpus</a></span></li><li><span><a href="#Parametrization-and-feature-extraction" data-toc-modified-id="Parametrization-and-feature-extraction-1.3"><span class="toc-item-num">1.3&nbsp;&nbsp;</span>Parametrization and feature extraction</a></span><ul class="toc-item"><li><span><a href="#Generating-N-gram-Feature-Combinations" data-toc-modified-id="Generating-N-gram-Feature-Combinations-1.3.1"><span class="toc-item-num">1.3.1&nbsp;&nbsp;</span>Generating N-gram Feature Combinations</a></span></li></ul></li><li><span><a href="#Frequency-threshold" data-toc-modified-id="Frequency-threshold-1.4"><span class="toc-item-num">1.4&nbsp;&nbsp;</span>Frequency threshold</a></span></li><li><span><a href="#Weighting-schemes" data-toc-modified-id="Weighting-schemes-1.5"><span class="toc-item-num">1.5&nbsp;&nbsp;</span>Weighting schemes</a></span></li><li><span><a href="#Classification-Process" data-toc-modified-id="Classification-Process-1.6"><span class="toc-item-num">1.6&nbsp;&nbsp;</span>Classification Process</a></span><ul class="toc-item"><li><span><a href="#Test-Prediction-and-Result-Evaluating-Fucntion" data-toc-modified-id="Test-Prediction-and-Result-Evaluating-Fucntion-1.6.1"><span class="toc-item-num">1.6.1&nbsp;&nbsp;</span>Test Prediction and Result Evaluating Fucntion</a></span></li><li><span><a href="#Initializing-classification-algorithms" data-toc-modified-id="Initializing-classification-algorithms-1.6.2"><span class="toc-item-num">1.6.2&nbsp;&nbsp;</span>Initializing classification algorithms</a></span></li><li><span><a href="#Cross-Validation-Classification-and-Evaluation-Function" data-toc-modified-id="Cross-Validation-Classification-and-Evaluation-Function-1.6.3"><span class="toc-item-num">1.6.3&nbsp;&nbsp;</span>Cross-Validation Classification and Evaluation Function</a></span></li></ul></li><li><span><a href="#End-to-End-Pipeline" data-toc-modified-id="End-to-End-Pipeline-1.7"><span class="toc-item-num">1.7&nbsp;&nbsp;</span>End-to-End Pipeline</a></span><ul class="toc-item"><li><span><a href="#Running-the-Experiment" data-toc-modified-id="Running-the-Experiment-1.7.1"><span class="toc-item-num">1.7.1&nbsp;&nbsp;</span>Running the Experiment</a></span></li></ul></li><li><span><a href="#Additional-Experiments-for-Paper" data-toc-modified-id="Additional-Experiments-for-Paper-1.8"><span class="toc-item-num">1.8&nbsp;&nbsp;</span>Additional Experiments for Paper</a></span><ul class="toc-item"><li><span><a href="#ROC-values-for-LinerSVC" data-toc-modified-id="ROC-values-for-LinerSVC-1.8.1"><span class="toc-item-num">1.8.1&nbsp;&nbsp;</span>ROC-values for LinerSVC</a></span></li><li><span><a href="#ROC-curves" data-toc-modified-id="ROC-curves-1.8.2"><span class="toc-item-num">1.8.2&nbsp;&nbsp;</span>ROC-curves</a></span></li></ul></li><li><span><a href="#Exp-for-EMNLP" data-toc-modified-id="Exp-for-EMNLP-1.9"><span class="toc-item-num">1.9&nbsp;&nbsp;</span>Exp for EMNLP</a></span></li></ul></li></ul></div>

# Fake news detection

In [1]:
# needed to make it run on Alisa's laptop -- ignore otherwise 
import sys 
#sys.executable, sys.path
sys.path.append('/Users/alisa/workspace/Urdu_Fake_News/envname/lib/python3.7/site-packages')

In [1]:
import re
import glob
import numpy as np
import os
import json
import argparse
import time
import codecs
import string
import codecs
import random
import scipy.sparse as sp
from pathlib import Path

from random import randrange
from scipy.sparse import csr_matrix, csc_matrix, hstack, coo_matrix
from gensim.matutils import Scipy2Corpus, corpus2csc
from gensim.models.logentropy_model import LogEntropyModel
from collections import defaultdict, Counter
from sklearn.svm import LinearSVC
from sklearn.svm import SVC
from sklearn.feature_extraction.text import CountVectorizer
from sklearn import preprocessing
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import train_test_split
from sklearn.naive_bayes import MultinomialNB
from sklearn.naive_bayes import GaussianNB
from sklearn.naive_bayes import BernoulliNB
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import classification_report, f1_score, make_scorer, accuracy_score
from sklearn.feature_extraction.text import TfidfTransformer
from nltk.corpus import stopwords as sw
from string import punctuation

D:\Anaconda\lib\site-packages\gensim\utils.py:1197: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


## Feature extraction functions

In [2]:
#Extracts word-ngrams, when n=1 is equal to bag of words
def wordNgrams(text, n):
    ngrams = []
    text = [word for word in text.split() if word not in string.punctuation]
    ngrams = [' '.join(text[i:i+n])+'' for i in range(len(text)-n+1)]
    return ngrams

In [3]:
text='پاکستان کے وزیراعظم عمران خان سعودی عرب کے دارالحکومت ریاض میں ملک میں سرمایہ کاری کے حوالے سے سالانہ کانفرنس میں شرکت کر رہے ہیں حکومت پاکستان کا کہنا ہے کہ سعودی عرب نے پاکستان کو معاشی بحران سے نمٹنے میں مدد کے لیے ایک سال کے لیے تین ارب ڈالر دینے پر اتفاق کیا ہے دفترِ خارجہ کی جانب سے منگل کی شب جاری ہونے والے اعلامیے میں بتایا گیا ہے کہ یہ فیصلہ'
#wordNgrams(text,2)

In [4]:
#Extracts character n-grams
def charNgrams(text, n):
    ngrams = []
    ngrams = [text[i:i+n]+'_cng' for i in range(len(text)-n+1)]
    return ngrams

In [5]:
charNgrams(text, 1)

['پ_cng',
 'ا_cng',
 'ک_cng',
 'س_cng',
 'ت_cng',
 'ا_cng',
 'ن_cng',
 ' _cng',
 'ک_cng',
 'ے_cng',
 ' _cng',
 'و_cng',
 'ز_cng',
 'ی_cng',
 'ر_cng',
 'ا_cng',
 'ع_cng',
 'ظ_cng',
 'م_cng',
 ' _cng',
 'ع_cng',
 'م_cng',
 'ر_cng',
 'ا_cng',
 'ن_cng',
 ' _cng',
 'خ_cng',
 'ا_cng',
 'ن_cng',
 ' _cng',
 'س_cng',
 'ع_cng',
 'و_cng',
 'د_cng',
 'ی_cng',
 ' _cng',
 'ع_cng',
 'ر_cng',
 'ب_cng',
 ' _cng',
 'ک_cng',
 'ے_cng',
 ' _cng',
 'د_cng',
 'ا_cng',
 'ر_cng',
 'ا_cng',
 'ل_cng',
 'ح_cng',
 'ک_cng',
 'و_cng',
 'م_cng',
 'ت_cng',
 ' _cng',
 'ر_cng',
 'ی_cng',
 'ا_cng',
 'ض_cng',
 ' _cng',
 'م_cng',
 'ی_cng',
 'ں_cng',
 ' _cng',
 'م_cng',
 'ل_cng',
 'ک_cng',
 ' _cng',
 'م_cng',
 'ی_cng',
 'ں_cng',
 ' _cng',
 'س_cng',
 'ر_cng',
 'م_cng',
 'ا_cng',
 'ی_cng',
 'ہ_cng',
 ' _cng',
 'ک_cng',
 'ا_cng',
 'ر_cng',
 'ی_cng',
 ' _cng',
 'ک_cng',
 'ے_cng',
 ' _cng',
 'ح_cng',
 'و_cng',
 'ا_cng',
 'ل_cng',
 'ے_cng',
 ' _cng',
 'س_cng',
 'ے_cng',
 ' _cng',
 'س_cng',
 'ا_cng',
 'ل_cng',
 'ا_cng',
 'ن_cng',


In [7]:
def load_diccionario(ruta):
    terms = set()#Dictionary of slangs
    try:
        tmp = open(ruta, "r", encoding="utf8")     
        while True :
            linea = tmp.readline()                                                                                   
            #linea = to_unicode(linea) 
            if (not linea) or (linea == ""):                                                                               
                break;                                                                                                      
            linea = linea.rstrip()
            terms.add(linea.lower())
        return (terms)
    except IOError as e:
        print ("Error: "+ruta+" I/O error({0}): {1}".format(e.errno, e.strerror))
        exit(1)

In [8]:
#Extracts function words n-grams with a pre-loaded dictionary
def funcNgrams(text, n):
    stop_words = load_diccionario('stop_words.txt')
    patt=r'\b(' + ('|'.join(re.escape(key) for key in stop_words)).lstrip('|') + r')\b'
    pattern = re.compile(patt)
    text = re.sub(r"(\n+|\r+|(\r\n)+)", " ", text)
    text = re.sub(r" +", " ", text)
    text = re.sub(r"’", "'", text)
    text = re.sub(r"[" + punctuation + "]*", "", text)
    terms = pattern.findall(text)
    n_grams=[('_'.join(terms[i:i+n])) + "_fwn" for i in range(len(terms)-n+1)]

    return n_grams

In [9]:
len(funcNgrams(text, 2))

35

In [10]:
def extract_features(text,cn,wn,fn):
    text = text.lower()
    #text=clean_text(text)
    features = []
    for n in wn:
        if n != 0:
            features.extend(wordNgrams(text,n))
    for n in cn:
        if n != 0:
            features.extend(charNgrams(text,n))
    for n in fn:
            if n != 0:
                features.extend(funcNgrams(text,n))
    return features

In [11]:
# Extracts all features in a set of 'texts' and return as a string separated with the simbol '&%$'
def process_texts(texts,cn,wn,fn):
    occurrences=defaultdict(int)
    featuresList=[]
    featuresDict=Counter()
    for (text) in texts:
        features=extract_features(text,cn,wn,fn)
        featuresDict.update(features)
        featuresList.append('&%$'.join(features))
    return featuresList, featuresDict

## Reading and preparing the corpus

In [12]:
def preprocessText(text):
    #here remove text
    cleantext=re.sub("\d+", "0", text)
    return cleantext

In [15]:
#utility function for reading files
def read_txt_files(files):
    text=[]
    topic=[]
    for i,file_path in enumerate(files):
        print('news',file_path)
        with open(file_path,'r', encoding="utf8") as infile:
            cleantext=preprocessText(infile.read())
            text.append(cleantext)
            #print(file_path)
            #file_topic=''.join(re.findall('[A-Za-z]',file_path.split('/')[3].split('.')[0]))
            file_topic=''.join(re.findall('[A-Za-z]', file_path.stem))
            #print (file_topic)
            topic.append(file_topic)
    return text, topic

In [16]:
#reading the path of real and fake news for training

# OS independent way to deal with files using Python3's library pathlib  (added do import)
# see: https://medium.com/@ageitgey/python-3-quick-tip-the-easy-way-to-deal-with-file-paths-on-windows-mac-and-linux-11a072b58d5f

# declaring paths using Python3's library pathlib
# train_path_real = Path('Corpus/Train/Real/')
# train_path_fake = Path('Corpus/Train/Fake/')

train_path_real = Path('CorpusMT/Train/Real/')
train_path_fake = Path('CorpusMT/Train/Fake/')

# list(p.glob('**/*.py'))
train_real_news, train_real_news_topics = read_txt_files(sorted(train_path_real.glob('*.txt')))
train_fake_news, train_fake_news_topics = read_txt_files(sorted(train_path_fake.glob('*.txt')))

news CorpusMT\Train\Real\biz01.legit.txt
news CorpusMT\Train\Real\biz02.legit.txt
news CorpusMT\Train\Real\biz03.legit.txt
news CorpusMT\Train\Real\biz04.legit.txt
news CorpusMT\Train\Real\biz05.legit.txt
news CorpusMT\Train\Real\biz06.legit.txt
news CorpusMT\Train\Real\biz07.legit.txt
news CorpusMT\Train\Real\biz08.legit.txt
news CorpusMT\Train\Real\biz09.legit.txt
news CorpusMT\Train\Real\biz10.legit.txt
news CorpusMT\Train\Real\biz11.legit.txt
news CorpusMT\Train\Real\biz12.legit.txt
news CorpusMT\Train\Real\biz13.legit.txt
news CorpusMT\Train\Real\biz14.legit.txt
news CorpusMT\Train\Real\biz15.legit.txt
news CorpusMT\Train\Real\biz16.legit.txt
news CorpusMT\Train\Real\biz17.legit.txt
news CorpusMT\Train\Real\biz18.legit.txt
news CorpusMT\Train\Real\biz19.legit.txt
news CorpusMT\Train\Real\biz20.legit.txt
news CorpusMT\Train\Real\biz21.legit.txt
news CorpusMT\Train\Real\biz22.legit.txt
news CorpusMT\Train\Real\biz23.legit.txt
news CorpusMT\Train\Real\biz24.legit.txt
news CorpusMT\Tr

news CorpusMT\Train\Fake\polit05.fake.txt
news CorpusMT\Train\Fake\polit06.fake.txt
news CorpusMT\Train\Fake\polit07.fake.txt
news CorpusMT\Train\Fake\polit08.fake.txt
news CorpusMT\Train\Fake\polit09.fake.txt
news CorpusMT\Train\Fake\polit10.fake.txt
news CorpusMT\Train\Fake\polit11.fake.txt
news CorpusMT\Train\Fake\polit12.fake.txt
news CorpusMT\Train\Fake\polit13.fake.txt
news CorpusMT\Train\Fake\polit14.fake.txt
news CorpusMT\Train\Fake\polit15.fake.txt
news CorpusMT\Train\Fake\polit16.fake.txt
news CorpusMT\Train\Fake\polit17.fake.txt
news CorpusMT\Train\Fake\polit18.fake.txt
news CorpusMT\Train\Fake\polit19.fake.txt
news CorpusMT\Train\Fake\polit20.fake.txt
news CorpusMT\Train\Fake\polit21.fake.txt
news CorpusMT\Train\Fake\polit22.fake.txt
news CorpusMT\Train\Fake\polit23.fake.txt
news CorpusMT\Train\Fake\polit24.fake.txt
news CorpusMT\Train\Fake\polit25.fake.txt
news CorpusMT\Train\Fake\polit26.fake.txt
news CorpusMT\Train\Fake\polit27.fake.txt
news CorpusMT\Train\Fake\polit28.f

In [17]:
#contatenating real and fake news in one variable for training
train_texts = np.concatenate((train_real_news, train_fake_news))

train_labels_real = np.concatenate((np.ones(len(train_real_news)), np.zeros(len(train_fake_news))))
# swapped real and fake 
train_labels_fake = np.concatenate((np.zeros(len(train_real_news)), np.ones(len(train_fake_news))))

train_topics = np.concatenate((train_real_news_topics, train_fake_news_topics))

In [18]:
print ('Train:')
print ('\t Real:',len(train_real_news))
print ('\t Fake:',len(train_fake_news))

Train:
	 Real: 140
	 Fake: 140


In [19]:
#reading the path of real and fake news for testing
#test_path_real = Path('Corpus/Test/Real/')
#test_path_fake = Path('Corpus/Test/Fake/')

test_path_real = Path('CorpusMT/Test/Real/')
test_path_fake = Path('CorpusMT/Test/Fake/')

real_news, real_news_topics = read_txt_files(sorted(test_path_real.glob('*.txt')))
fake_news, fake_news_topics = read_txt_files(sorted(test_path_fake.glob('*.txt')))

#contatenating real and fake news in one variable for testing
test_texts = np.concatenate((real_news, fake_news))
test_labels_real = np.concatenate((np.ones(len(real_news)), np.zeros(len(fake_news))))
test_labels_fake = np.concatenate((np.zeros(len(real_news)), np.ones(len(fake_news))))
test_topics = np.concatenate((real_news_topics, fake_news_topics))

news CorpusMT\Test\Real\biz29.legit.txt
news CorpusMT\Test\Real\biz30.legit.txt
news CorpusMT\Test\Real\biz31.legit.txt
news CorpusMT\Test\Real\biz32.legit.txt
news CorpusMT\Test\Real\biz33.legit.txt
news CorpusMT\Test\Real\biz34.legit.txt
news CorpusMT\Test\Real\biz35.legit.txt
news CorpusMT\Test\Real\biz36.legit.txt
news CorpusMT\Test\Real\biz37.legit.txt
news CorpusMT\Test\Real\biz38.legit.txt
news CorpusMT\Test\Real\biz39.legit.txt
news CorpusMT\Test\Real\biz40.legit.txt
news CorpusMT\Test\Real\entmt29.legit.txt
news CorpusMT\Test\Real\entmt30.legit.txt
news CorpusMT\Test\Real\entmt31.legit.txt
news CorpusMT\Test\Real\entmt32.legit.txt
news CorpusMT\Test\Real\entmt33.legit.txt
news CorpusMT\Test\Real\entmt34.legit.txt
news CorpusMT\Test\Real\entmt35.legit.txt
news CorpusMT\Test\Real\entmt36.legit.txt
news CorpusMT\Test\Real\entmt37.legit.txt
news CorpusMT\Test\Real\entmt38.legit.txt
news CorpusMT\Test\Real\entmt39.legit.txt
news CorpusMT\Test\Real\entmt40.legit.txt
news CorpusMT\Te

In [38]:
print ('Test:')
print ('\t Real:',len(real_news))
print ('\t Fake:',len(fake_news))

Test:
	 Real: 60
	 Fake: 60


In [39]:
train_labels_dict = {'real': train_labels_real, 'fake': train_labels_fake}
test_labels_dict = {'real': test_labels_real, 'fake': test_labels_fake}

## Parametrization and feature extraction

### Generating N-gram Feature Combinations

We're generating a few sets of experiments with different varyingvalues of N-grams for each feature type and their combinations.  This looks like incomplete exhaustive search because we actually don't consider (at least so far) _all_ possible combinations that sрould be roughly 3^6 = 729 and then multiply by varios normalization techniques by various classifiers. 

We actually can do it yet I am not sure whether it'll make sense and maybe there's a better "smart grid search"  strategy when we first lok at some parameter combination, then find the best and then look at other possible variations around that point of parameter values.  

In [16]:
# Generating 60 combinations of char-word-func N-grams
# [cnvalues, wnvalues, fnvalues]
num_feat_types = 3 
ngram_feat_combinations = [[], [], []]

# for a single type n-grams
for j in range(num_feat_types): 
    for i in range(1,7):
        ngram_feat_combinations[j].append([i])
        for k in range(num_feat_types): 
            if k != j: 
                ngram_feat_combinations[k].append([0])
        
# extending with 1-1-1, 2-2-2,3-3-3,4-4-4,5-5-5,6-6-6 variants
ngrams = [[x] for x in range(1,7)]

for ngram_type in ngram_feat_combinations: 
    ngram_type.extend(ngrams)
    
# combinations of varying X-grams - uni-Y
for l in range(num_feat_types):
    for j in range(num_feat_types):
        if j != l: 
            for i in range(1,7):
                ngram_feat_combinations[l].append([i])
                ngram_feat_combinations[j].append([1])    
                for k in range(num_feat_types):                 
                    if k != j and k != l: 
                        ngram_feat_combinations[k].append([0])       
        
len(ngram_feat_combinations[0])                        

60

In [100]:
# show the generated feature combinations:  
for i in range(10):     
        for feat in ngram_feat_combinations:
                print(feat[i*6 : i*6+6])
        print()        

[[1], [2], [3], [4], [5], [6]]
[[0], [0], [0], [0], [0], [0]]
[[0], [0], [0], [0], [0], [0]]

[[0], [0], [0], [0], [0], [0]]
[[1], [2], [3], [4], [5], [6]]
[[0], [0], [0], [0], [0], [0]]

[[0], [0], [0], [0], [0], [0]]
[[0], [0], [0], [0], [0], [0]]
[[1], [2], [3], [4], [5], [6]]

[[1], [2], [3], [4], [5], [6]]
[[1], [2], [3], [4], [5], [6]]
[[1], [2], [3], [4], [5], [6]]

[[1], [2], [3], [4], [5], [6]]
[[1], [1], [1], [1], [1], [1]]
[[0], [0], [0], [0], [0], [0]]

[[1], [2], [3], [4], [5], [6]]
[[0], [0], [0], [0], [0], [0]]
[[1], [1], [1], [1], [1], [1]]

[[1], [1], [1], [1], [1], [1]]
[[1], [2], [3], [4], [5], [6]]
[[0], [0], [0], [0], [0], [0]]

[[0], [0], [0], [0], [0], [0]]
[[1], [2], [3], [4], [5], [6]]
[[1], [1], [1], [1], [1], [1]]

[[1], [1], [1], [1], [1], [1]]
[[0], [0], [0], [0], [0], [0]]
[[1], [2], [3], [4], [5], [6]]

[[0], [0], [0], [0], [0], [0]]
[[1], [1], [1], [1], [1], [1]]
[[1], [2], [3], [4], [5], [6]]



In [20]:
# the class is required to enable proper use of the feature extraction functionality in the experiment pipeline
class FeatureExtractor: 
    """Feature extraction"""
    
    def __init__(self, cnvalues, wnvalues, fnvalues): 
        print('Feature extractor for ' + str(cnvalues[0]) +'-' + str(wnvalues[0]) + '-' + str(fnvalues[0]) + ' char-word-func N-gram combination')
        self.cnvalues = cnvalues
        self.wnvalues = wnvalues
        self.fnvalues = fnvalues
        
        self.vectorizer = CountVectorizer(lowercase=False, min_df=2, tokenizer=lambda x: x.split('&%$')) #--> we can change this
        
    def fit_extract(self, train_texts):
        train_features, dicOfFeatures = process_texts(train_texts, self.cnvalues, self.wnvalues, self.fnvalues)
        train_data = self.vectorizer.fit_transform(train_features)
        train_data = train_data.astype(float)
        return train_data, dicOfFeatures
    
    def extract(self, test_texts): 
        test_features, dicOfFeaturesTest = process_texts(test_texts, self.cnvalues, self.wnvalues, self.fnvalues)
        test_data = self.vectorizer.transform(test_features)
        test_data = test_data.astype(float)
        return test_data, dicOfFeaturesTest            

## Frequency threshold

In [21]:
def apply_frequency_threshold(feature_mx, N=5):
    values=np.array(feature_mx.sum(axis=0)).ravel()
    thresholdMask=(values >= N)*1
    indices_zero = list(np.nonzero(thresholdMask == 0)[0])
    all_cols = np.arange(feature_mx.shape[1])
    cols_to_keep = np.where(np.logical_not(np.in1d(all_cols, indices_zero)))[0]
    return cols_to_keep 

# to use: 
#cols_to_keep = apply_frequency_threshold(train_feature_mx)
#thresholded_train_feat_mx = train_feature_mx[:, cols_to_keep]
#thresholded_test_feat_mx = test_feature_mx[:, cols_to_keep]

## Weighting schemes

In [22]:
# possible values: binary, logent, tfidf, norm, relat
weighting_schemes = ['binary', 'logent', 'tfidf', 'norm', 'relat', 'none (tf)']

In [23]:
from gensim.matutils import Scipy2Corpus, corpus2csc
from gensim.models.logentropy_model import LogEntropyModel

class LogEntWeightScheme: 
        
    def __init__(self): 
        self.log_ent = None
        self.train_data_shape = 1
        
    def fit(self, scaled_train_data, *_):
        Xc = Scipy2Corpus(scaled_train_data)
        self.log_ent = LogEntropyModel(Xc)
        X = self.log_ent[Xc]
        X = corpus2csc(X)
        scaled_train_data = sp.csc_matrix.transpose(X)
        self.train_data_shape = scaled_train_data.shape[1]
        return scaled_train_data
        
    def fit_transform(self, scaled_train_data, *_):    
        Xc = Scipy2Corpus(scaled_train_data)
        self.log_ent = LogEntropyModel(Xc)
        X = self.log_ent[Xc]
        X = corpus2csc(X)
        scaled_train_data = sp.csc_matrix.transpose(X)
        self.train_data_shape = scaled_train_data.shape[1]
        return scaled_train_data 

    def transform(self, scaled_test_data, *_):
        Xtest = Scipy2Corpus(scaled_test_data)
        X = self.log_ent[Xtest]
        X = corpus2csc(X, self.train_data_shape)
        scaled_test_data = sp.csc_matrix.transpose(X)
        return scaled_test_data
        

In [24]:
from scipy.sparse import coo_matrix

class RelativeWeightScheme:
    
    def __init__(self):
        self.s = 1.0
             
    def fit(self, scaled_train_data, *_):
        self.s = scaled_train_data.sum(axis=0)
        scaled_train_data = coo_matrix(np.nan_to_num(scaled_train_data/self.s), dtype=np.float64)
        return scaled_train_data

    # identical to fit()
    def fit_transform(self, scaled_train_data, *_):
        self.s = scaled_train_data.sum(axis=0)
        scaled_train_data = coo_matrix(np.nan_to_num(scaled_train_data/self.s), dtype=np.float64)
        return scaled_train_data
                
    def transform(self, scaled_test_data, *_):          
        scaled_test_data = coo_matrix(np.nan_to_num(scaled_test_data/self.s), dtype=np.float64)
        return scaled_test_data    

In [25]:
class DoNothingWeightScheme:
    """Making it easier to comply with APIs for a do-nothing trasnformer"""

    def __init__(self):
        pass
    
    def fit(self, scaled_train_data, *_):
        return scaled_train_data

    def fit_transform(self, scaled_train_data, *_):
        return scaled_train_data

    def transform(self, scaled_test_data, *_):
        return scaled_test_data
       

In [26]:
def get_weighting_scheme(feature_weight_name): 
    
    if feature_weight_name == 'binary':
        print ("feature_weight = binary")
        return preprocessing.Binarizer()

    elif feature_weight_name == 'logent':
        print ("feature_weight = logent")
        return LogEntWeightScheme()
        
    elif feature_weight_name == 'tfidf':
        print ("feature_weight = tfidf")
        return TfidfTransformer()

    elif feature_weight_name == 'norm':
        # cannot normalize with l2 in a Pipeline
        print ("feature_weight = norm")
        return preprocessing.MaxAbsScaler()

    elif feature_weight_name == 'relat':
        print ("feature_weight = relat")
        return RelativeWeightScheme()

    else:
        print ("feature_weight = tf")
        return DoNothingWeightScheme()         

## Classification Process

### Test Prediction and Result Evaluating Fucntion

In [29]:
from sklearn.metrics import accuracy_score, f1_score, roc_auc_score, recall_score, precision_score
from sklearn.metrics import confusion_matrix
from sklearn.metrics import balanced_accuracy_score
from IPython.display import display
from mlxtend.plotting import plot_decision_regions

def check_model_fit(clf, X_test, y_test):
    # Print overall test-set accuracy
    y_pred = clf.predict(X_test)
    acc = accuracy_score(y_test, y_pred, normalize=True)

    p = precision_score(y_test, y_pred)
    r = recall_score(y_test, y_pred)
    f1 = f1_score(y_test, y_pred)
       
    balanced_acc = balanced_accuracy_score(y_test, y_pred)     
    
    roc_auc = 0.0
    y_pred_scores = []
    if hasattr(clf, 'predict_proba'): 
        y_pred_scores = clf.predict_proba(X_test)
        roc_auc = roc_auc_score(y_test, y_pred_scores[:, 1])        
    
    # Print confusion matrix
    #cmat = confusion_matrix(y_test, y_pred)
    #cols = pd.MultiIndex.from_tuples([('predictions', 0), ('predictions', 1)])
    #indx = pd.MultiIndex.from_tuples([('actual', 0), ('actual', 1)])
    #display(pd.DataFrame(cmat, columns=cols, index=indx))
    #print()
    
    # Print test-set accuracy grouped by the target variable 
    #print('percent accuracy score per class:')
    #cmat = confusion_matrix(y_test, y_pred)
    #scores = cmat.diagonal() / cmat.sum(axis=1) * 100
    # specificity: 
    #irrelevant_acc = scores[0]
    # sensetivity:  
    #relevant_acc = scores[1]
    #balanced_acc = (relevant_acc + irrelevant_acc)/2.0
    #print('left = 0 : {:.2f}%'.format(scores[0]))
    #print('left = 1 : {:.2f}%'.format(scores[1]))
    #print()
    
    # Plot decision regions
    #fig = plt.figure(figsize=(8, 8))
    #N_samples = 200
    #X, y = X_test[:N_samples], y_test[:N_samples]
    #plot_decision_regions(X, y, clf=clf)
    
    #plt.xlabel('satisfaction_level')
    #plt.ylabel('last_evaluation')
    #plt.legend(loc='upper left')
    
    results = {'accuracy': acc, 
               'balanced_accuracy': balanced_acc, 
               'precision': p, 
               'recall': r, 
               'f1': f1, 
               'roc_auc': roc_auc}
    
    return results, y_pred_scores
    

In [50]:
from sklearn.metrics import accuracy_score, f1_score, roc_auc_score, recall_score, precision_score
from sklearn.metrics import confusion_matrix
#from sklearn.metrics import balanced_accuracy_score
#from IPython.display import display
#from mlxtend.plotting import plot_decision_regions

def check_model_fit_no_bal_acc(clf, X_test, y_test):
    # Print overall test-set accuracy
    y_pred = clf.predict(X_test)
    acc = accuracy_score(y_test, y_pred, normalize=True)

    p = precision_score(y_test, y_pred)
    r = recall_score(y_test, y_pred)
    f1 = f1_score(y_test, y_pred)
       
    #balanced_acc = balanced_accuracy_score(y_test, y_pred)     
    
    roc_auc = 0.0
    y_pred_scores = []
    if hasattr(clf, 'predict_proba'): 
        y_pred_scores = clf.predict_proba(X_test)
        roc_auc = roc_auc_score(y_test, y_pred_scores[:, 1])        
    
    # Print confusion matrix
    #cmat = confusion_matrix(y_test, y_pred)
    #cols = pd.MultiIndex.from_tuples([('predictions', 0), ('predictions', 1)])
    #indx = pd.MultiIndex.from_tuples([('actual', 0), ('actual', 1)])
    #display(pd.DataFrame(cmat, columns=cols, index=indx))
    #print()
    
    # Print test-set accuracy grouped by the target variable 
    #print('percent accuracy score per class:')
    #cmat = confusion_matrix(y_test, y_pred)
    #scores = cmat.diagonal() / cmat.sum(axis=1) * 100
    # specificity: 
    #irrelevant_acc = scores[0]
    # sensetivity:  
    #relevant_acc = scores[1]
    #balanced_acc = (relevant_acc + irrelevant_acc)/2.0
    #print('left = 0 : {:.2f}%'.format(scores[0]))
    #print('left = 1 : {:.2f}%'.format(scores[1]))
    #print()
    
    # Plot decision regions
    #fig = plt.figure(figsize=(8, 8))
    #N_samples = 200
    #X, y = X_test[:N_samples], y_test[:N_samples]
    #plot_decision_regions(X, y, clf=clf)
    
    #plt.xlabel('satisfaction_level')
    #plt.ylabel('last_evaluation')
    #plt.legend(loc='upper left')
    
    results = {'accuracy': acc, 
               #'balanced_accuracy': balanced_acc, 
               'precision': p, 
               'recall': r, 
               'f1': f1, 
               'roc_auc': roc_auc}
    
    return results, y_pred_scores
    

### Initializing classification algorithms

In [30]:
# AZ:  I don't think we need to balance the classes: 
# first, the data is not so heavily imbalanced 
# second, we loose the class distribution information  

from sklearn.linear_model import LogisticRegression
from sklearn.svm import LinearSVC
from sklearn.svm import SVC
from sklearn.tree import DecisionTreeClassifier
from sklearn.naive_bayes import MultinomialNB, BernoulliNB
from sklearn.ensemble.forest import RandomForestClassifier
from sklearn.ensemble.weight_boosting import AdaBoostClassifier

clfLG = LogisticRegression(solver='lbfgs', tol=0.001, C=0.01)
clfLinSVM = LinearSVC(C=0.01, random_state=85)
clfSVC = SVC(C=0.01, kernel='linear')
clfDT = DecisionTreeClassifier(random_state=0)
clfRFC = RandomForestClassifier(n_estimators=100, max_depth=2, random_state=0)
clfMnb = MultinomialNB()
clfBnb = BernoulliNB()
clfAB = AdaBoostClassifier(base_estimator=None, n_estimators=50, learning_rate=1.0,  random_state=None)

# clfs = [clfLG, clfLinSVM, clfSVC, clfDT, clfRFC, clfMnb, clfBnb,  clfAB]

### Cross-Validation Classification and Evaluation Function

In [31]:
from sklearn.model_selection import cross_validate

def cv(clf, train_X, train_y, scoring=['accuracy', 'balanced_accuracy' ,'precision', 'recall', 'f1', 'roc_auc']): 
    cv = cross_validate(clf, train_X, train_y, cv=5, return_estimator=True, scoring=scoring)
    
    output = {}
    for s in scoring: 
        m = np.mean(cv['test_' + s])
        v = np.var(cv['test_' + s])
        output[s] ={'mean': m, 'var': v}      
    return output

In [32]:
from sklearn.model_selection import cross_validate

def cv(clf, train_X, train_y, scoring=['accuracy', 'precision', 'recall', 'f1', 'roc_auc']): 
    cv = cross_validate(clf, train_X, train_y, cv=5, return_estimator=True, scoring=scoring)
    
    output = {}
    for s in scoring: 
        m = np.mean(cv['test_' + s])
        v = np.var(cv['test_' + s])
        output[s] ={'mean': m, 'var': v}      
    return output

## End-to-End Pipeline

The pipeline function `end_to_end` allows to run an verall experiemnt (apart from the text corpus read-in) easily by specifying the desired patrameters for an experiment: 

* n_gram_feature set  (see the specific format)
* list of weighting schemes
* list of classifiers 

Use the default values as sample examples and see the running example in the cells below.  

Beware that the train and test text sets along with teh training labels packed as a dictionary should be provided

In [47]:
# the end to end experiment pipeline. See below how to run it  
from sklearn.pipeline import Pipeline
import pandas as pd 

def end_to_end(train_texts, train_labels_dict, test_texts, test_labels_dict, 
             ngram_feat_sets=[[[1]],[[0]],[[0]]], weight_schemes=['binary'], clfs=[clfLG], 
             expLog_df=pd.DataFrame(columns=['N-gram-feat-comb', 'char N-gram', 'word N-gram', 'func N-gram'  , 'total_feat_num', 'weight scheme', 'classifier', 'cv-acc', 'cv-balanced_acc','cv-roc', 'cv-f1-fake', 'acc', 'balanced_acc', 'roc', 'f1_fake', 'f1_real']), 
             name_prefix=''):  
    
    all_experiments = {}
    
    cv_scores_stub = {'accuracy': {'mean': -1, 'var': -1},
                        'balanced_accuracy': {'mean': -1, 'var': -1},
                        'precision': {'mean': -1, 'var': -1} ,
                        'recall': {'mean': -1, 'var': -1},
                        'f1': {'mean': -1, 'var': -1},
                        'roc_auc': {'mean': -1, 'var': -1}}
    
    testing_score_stub = {'accuracy': -1, 
                           'balanced_accuracy': -1, 
                           'precision': -1, 
                           'recall': -1, 
                           'f1': -1, 
                           'roc_auc': -1}
    
    
    # for each combination of ngram feature types
    for i in range(len(ngram_feat_sets[0])):         
        cnvalues = ngram_feat_sets[0][i]
        wnvalues = ngram_feat_sets[1][i] 
        fnvalues = ngram_feat_sets[2][i] 
        ngram_feat_type_set_str = str(cnvalues[0]) +'-' + str(wnvalues[0]) + '-' + str(fnvalues[0]) + ' char-word-func'
        char_n_gram = cnvalues[0]
        word_n_gram = wnvalues[0]
        func_n_gram = fnvalues[0]
        
        feat_extractor = FeatureExtractor(cnvalues, wnvalues, fnvalues)        
        train_feature_mx, _ = feat_extractor.fit_extract(train_texts)
        test_feature_mx, _ = feat_extractor.extract(test_texts) 
        print('train shape: ', train_feature_mx.shape, 'test shape:', test_feature_mx.shape)
        
        #applying the frequency threshold
        cols_to_keep = apply_frequency_threshold(train_feature_mx)
        thresholded_train_feat_mx = train_feature_mx[:, cols_to_keep]
        thresholded_test_feat_mx = test_feature_mx[:, cols_to_keep]
        
        #for each weighting scheme, for each classifier, create a pipeline
        pipelines = []
        
        all_experiments[ngram_feat_type_set_str] = {}
        for weight_scheme_name in weight_schemes: 
            all_experiments[ngram_feat_type_set_str][weight_scheme_name] = {}
            weight_scheme = get_weighting_scheme(weight_scheme_name)
            for clf in clfs: 
                clf_name = type(clf).__name__
                print('Classifier: ' + clf_name)
                all_experiments[ngram_feat_type_set_str][weight_scheme_name][clf_name] = {}
                ppl = Pipeline([('scaler', weight_scheme), ('clf', clf)])

                cv_scores_by_labeling = {}
                test_scores_by_labeling = {}
                for key in train_labels_dict:
                    print(key + " run...")
                    train_X = thresholded_train_feat_mx.copy()
                    train_X_cv = thresholded_train_feat_mx.copy()
                    test_X = thresholded_test_feat_mx.copy() 

                    train_y = train_labels_dict[key]
                    test_y = test_labels_dict[key]
                    
                    # cross-validation run 
                    # scoring=['accuracy', 'balanced_accuracy' ,'precision', 'recall', 'f1', 'roc_auc']
                    try: 
                        cv_scores = cv(ppl, train_X_cv, train_y)
                    except Exception as e: 
                        print(e)
                        cv_scores = cv_scores_stub                        
                    cv_scores_by_labeling[key] = cv_scores
                    
                    # test run 
                    try: 
                        ppl.fit(train_X, train_y)
                        #acc, balanced_acc, p, r, f1, roc_auc
                        test_scores, _ = check_model_fit(ppl, test_X, test_y)
                    except Exception as e: 
                        print(e)
                        test_scores = test_scores_stub                        
                    test_scores_by_labeling[key] = test_scores
                
                all_experiments[ngram_feat_type_set_str][weight_scheme_name][clf_name]['cv'] = cv_scores_by_labeling
                all_experiments[ngram_feat_type_set_str][weight_scheme_name][clf_name]['test'] = test_scores_by_labeling
                                
                # record experiments to the log 
                #['N-gram-feat-comb', 'total_feat_num', 'weight scheme', 'classifier', 
                # 'cv-acc', 'cv-balanced_acc','cv-roc', 'cv-f1-fake', 
                # 'acc', 'balanced_acc', 'roc', 'f1_fake', 'f1_real']
                expLog_df.loc[len(expLog_df)] = [name_prefix + ngram_feat_type_set_str, char_n_gram, word_n_gram, func_n_gram, thresholded_train_feat_mx.shape[1], weight_scheme_name, clf_name,
                                           np.round(cv_scores_by_labeling['fake']['accuracy']['mean'], 2), np.round(cv_scores_by_labeling['fake']['balanced_accuracy']['mean'], 2), np.round(cv_scores_by_labeling['fake']['roc_auc']['mean'], 2), np.round(cv_scores_by_labeling['fake']['f1']['mean'], 2), 
                                           np.round(test_scores_by_labeling['fake']['accuracy'], 2), np.round(test_scores_by_labeling['fake']['balanced_accuracy'], 2), np.round(test_scores_by_labeling['fake']['roc_auc'], 2), np.round(test_scores_by_labeling['fake']['f1'], 2), np.round(test_scores_by_labeling['real']['f1'], 2)]
                
                expLog_df
                
    return all_experiments, expLog_df

### Running the Experiment

In [ ]:
# creating the Export Log dataframe in the following format 
import pandas as pd 

my_expLog = pd.DataFrame(columns=['N-gram-feat-comb', 'char N-gram', 'word N-gram', 'func N-gram'  , 'total_feat_num', 'weight scheme', 'classifier', 'cv-acc', 'cv-balanced_acc','cv-roc', 'cv-f1-fake', 'acc', 'balanced_acc', 'roc', 'f1_fake', 'f1_real'])

In [85]:
# define your feature combination in format:   [[[1]],  [[0]], [[0]]]  for 1-0-0 char-word-func (note the brakets)
# 2 sets of experiments will look like:  [[[1], [2]],  [[0], [1]], [[0], [2]]] for 1-0-0 and 2-1-2 experiments 
#
my_ngram_feat_combinations = ngram_feat_combinations

# specify the weighting schemes you want to use from the list: 
# weighting_schemes = ['binary', 'logent', 'tfidf', 'norm', 'relat', 'none (tf)']
my_weighting_schemes = ['tfidf', 'norm', 'relat', 'none (tf)']

# specify the classifiers you want to use form the list:  
# [clfLG, clfLinSVM, clfSVC, clfDT, clfRFC, clfMnb, clfBnb,  clfAB]
my_clfs = [clfLG, clfLinSVM, clfSVC, clfDT, clfRFC, clfMnb, clfBnb,  clfAB]

# run the experiments
all_results_logent, expLog = end_to_end(train_texts, train_labels_dict, test_texts, test_labels_dict, 
             my_ngram_feat_combinations, my_weighting_schemes, my_clfs, 
             my_expLog)

Feature extractor for 1-0-0 char-word-func N-gram combination
train shape:  (638, 110) test shape: (262, 110)
feature_weight = tfidf
Classifier: LogisticRegression
real run...
fake run...


/Users/alisa/workspace/Urdu_Fake_News/envname/lib/python3.7/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/alisa/workspace/Urdu_Fake_News/envname/lib/python3.7/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/alisa/workspace/Urdu_Fake_News/envname/lib/python3.7/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/alisa/workspace/Urdu_Fake_News/envname/lib/python3.7/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precisio

Classifier: LinearSVC
real run...
fake run...


/Users/alisa/workspace/Urdu_Fake_News/envname/lib/python3.7/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/alisa/workspace/Urdu_Fake_News/envname/lib/python3.7/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/alisa/workspace/Urdu_Fake_News/envname/lib/python3.7/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/alisa/workspace/Urdu_Fake_News/envname/lib/python3.7/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precisio

Classifier: SVC
real run...
fake run...


...

Input contains NaN, infinity or a value too large for dtype('float32').
fake run...


/Users/alisa/workspace/Urdu_Fake_News/envname/lib/python3.7/site-packages/scipy/sparse/base.py:597: RuntimeWarning: invalid value encountered in true_divide
  return np.true_divide(self.todense(), other)
/Users/alisa/workspace/Urdu_Fake_News/envname/lib/python3.7/site-packages/scipy/sparse/base.py:597: RuntimeWarning: divide by zero encountered in true_divide
  return np.true_divide(self.todense(), other)
/Users/alisa/workspace/Urdu_Fake_News/envname/lib/python3.7/site-packages/scipy/sparse/base.py:597: RuntimeWarning: invalid value encountered in true_divide
  return np.true_divide(self.todense(), other)


Input contains NaN, infinity or a value too large for dtype('float32').
feature_weight = tf
Classifier: LogisticRegression
real run...
fake run...
Classifier: LinearSVC
real run...
fake run...
Classifier: SVC
real run...
fake run...
Classifier: DecisionTreeClassifier
real run...
fake run...
Classifier: RandomForestClassifier
real run...
fake run...


/Users/alisa/workspace/Urdu_Fake_News/envname/lib/python3.7/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/alisa/workspace/Urdu_Fake_News/envname/lib/python3.7/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/alisa/workspace/Urdu_Fake_News/envname/lib/python3.7/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/alisa/workspace/Urdu_Fake_News/envname/lib/python3.7/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precisio

Classifier: MultinomialNB
real run...
fake run...
Classifier: BernoulliNB
real run...
fake run...
Classifier: AdaBoostClassifier
real run...
fake run...


In [128]:
# writing the Experiment Log to a .csv file (to be read as a DataFrame for analysis in a separate notebook)
expLog.to_csv(Path('results/results.csv'), index=False)

In [108]:
# writing a more detailed report as .JSON file to be read as Python dictionary object (contains more metrics)
json.dump(all_results_logent, open(Path('results/results-tfidf-norm-relat-tf.json'), 'w'))

In [129]:
expLog.head(20)

N-gram-feat-comb  char N-gram  word N-gram  func N-gram  \
0   1-0-0 char-word-func            1            0            0   
1   1-0-0 char-word-func            1            0            0   
2   1-0-0 char-word-func            1            0            0   
3   1-0-0 char-word-func            1            0            0   
4   1-0-0 char-word-func            1            0            0   
5   1-0-0 char-word-func            1            0            0   
6   1-0-0 char-word-func            1            0            0   
7   1-0-0 char-word-func            1            0            0   
8   1-0-0 char-word-func            1            0            0   
9   1-0-0 char-word-func            1            0            0   
10  1-0-0 char-word-func            1            0            0   
11  1-0-0 char-word-func            1            0            0   
12  1-0-0 char-word-func            1            0            0   
13  1-0-0 char-word-func            1            0            0   
14  1-0-0 char-word-func            1            0            0   
15  1-0-0 char-word-func            1            0            0   
16  1-0-0 char-word-func            1            0            0   
17  1-0-0 char-word-func            1            0            0   
18  1-0-0 char-word-func            1            0            0   
19  1-0-0 char-word-func            1            0            0   

   total_feat_num weight scheme              classifier  cv-acc  \
0             101        binary      LogisticRegression    0.66   
1             101        binary      LogisticRegression    0.66   
2             101        binary               LinearSVC    0.73   
3             101        binary                     SVC    0.67   
4             101        binary  DecisionTreeClassifier    0.72   
5             101        binary  RandomForestClassifier    0.65   
6             101        binary           MultinomialNB    0.64   
7             101        binary             BernoulliNB    0.66   
8             101        binary      AdaBoostClassifier    0.70   
9             101        binary      LogisticRegression    0.66   
10            101        binary               LinearSVC    0.73   
11            101        binary                     SVC    0.67   
12            101        binary  DecisionTreeClassifier    0.72   
13            101        binary  RandomForestClassifier    0.65   
14            101        binary           MultinomialNB    0.64   
15            101        binary             BernoulliNB    0.66   
16            101        binary      AdaBoostClassifier    0.69   
17            101        binary      LogisticRegression    0.66   
18            101        binary               LinearSVC    0.73   
19            101        binary                     SVC    0.67   

    cv-balanced_acc  cv-roc  cv-f1-fake   acc  balanced_acc   roc  f1_fake  \
0              0.64    0.79        0.52  0.75          0.72  0.85     0.65   
1              0.64    0.79        0.52  0.75          0.72  0.85     0.65   
2              0.73    0.81        0.72  0.80          0.79  0.00     0.76   
3              0.64    0.79        0.46  0.77          0.75  0.00     0.68   
4              0.72    0.72        0.68  0.77          0.76  0.78     0.72   
5              0.61    0.80        0.32  0.72          0.68  0.89     0.52   
6              0.66    0.77        0.70  0.66          0.69  0.82     0.69   
7              0.68    0.76        0.71  0.69          0.71  0.82     0.71   
8              0.69    0.76        0.67  0.78          0.77  0.90     0.73   
9              0.64    0.79        0.52  0.75          0.72  0.85     0.65   
10             0.73    0.81        0.72  0.80          0.79  0.00     0.76   
11             0.64    0.79        0.46  0.77          0.75  0.00     0.68   
12             0.72    0.72        0.68  0.77          0.76  0.78     0.72   
13             0.61    0.80        0.32  0.72          0.68  0.89     0.52   
14             0.66   

## Additional Experiments for Paper

### ROC-values for LinerSVC

In [35]:
from sklearn.calibration import CalibratedClassifierCV

isotonic_svc = CalibratedClassifierCV(
    base_estimator=clfLinSVM,
    method='isotonic'
) # isotonic calibration

#isotonic_svc.fit(X_train, y_train)
#y_prob = isotonic_svc.predict_proba(X_test)

In [40]:
from sklearn.pipeline import Pipeline

cnvalues = [3] #[3]
wnvalues = [3] #[0]
fnvalues = [3] #[1]

weight_scheme_name = 'norm'#'binary'

isotonic_svc = CalibratedClassifierCV(
    base_estimator=clfLinSVM,
    method='isotonic'
)
clf = isotonic_svc


ngram_feat_type_set_str = str(cnvalues[0]) +'-' + str(wnvalues[0]) + '-' + str(fnvalues[0]) + ' char-word-func'
char_n_gram = cnvalues[0]
word_n_gram = wnvalues[0]
func_n_gram = fnvalues[0]

feat_extractor = FeatureExtractor(cnvalues, wnvalues, fnvalues)        
train_feature_mx, _ = feat_extractor.fit_extract(train_texts)
test_feature_mx, _ = feat_extractor.extract(test_texts) 
print('train shape: ', train_feature_mx.shape, 'test shape:', test_feature_mx.shape)

#applying the frequency threshold
cols_to_keep = apply_frequency_threshold(train_feature_mx)
thresholded_train_feat_mx = train_feature_mx[:, cols_to_keep]
thresholded_test_feat_mx = test_feature_mx[:, cols_to_keep]
print('Thresholded train shape: ', thresholded_train_feat_mx.shape, 'test shape:', thresholded_test_feat_mx.shape)

weight_scheme = get_weighting_scheme(weight_scheme_name)
ppl = Pipeline([('scaler', weight_scheme), ('clf', clf)])

cv_scores_by_labeling = {}
test_scores_by_labeling = {}
for key in train_labels_dict:
    print(key + " run...")
    train_X = thresholded_train_feat_mx.copy()
    train_X_cv = thresholded_train_feat_mx.copy()
    test_X = thresholded_test_feat_mx.copy() 

    train_y = train_labels_dict[key]
    test_y = test_labels_dict[key]

    # cross-validation run 
    # scoring=['accuracy', 'balanced_accuracy' ,'precision', 'recall', 'f1', 'roc_auc']
    try: 
        cv_scores = cv(ppl, train_X_cv, train_y)
    except Exception as e: 
        print(e)
        cv_scores = cv_scores_stub                        
    cv_scores_by_labeling[key] = cv_scores

    # test run 
    try: 
        ppl.fit(train_X, train_y)
        #acc, balanced_acc, p, r, f1, roc_auc
        test_scores, _ = check_model_fit(ppl, test_X, test_y)
    except Exception as e: 
        print(e)
        test_scores = test_scores_stub                        
    test_scores_by_labeling[key] = test_scores        

Feature extractor for 3-3-3 char-word-func N-gram combination
train shape:  (280, 13574) test shape: (120, 13574)
Thresholded train shape:  (280, 5294) test shape: (120, 5294)
feature_weight = norm
real run...


D:\Anaconda\lib\site-packages\sklearn\model_selection\_split.py:1978: FutureWarning: The default value of cv will change from 3 to 5 in version 0.22. Specify it explicitly to silence this warning.
  warnings.warn(CV_WARNING, FutureWarning)
D:\Anaconda\lib\site-packages\sklearn\model_selection\_split.py:1978: FutureWarning: The default value of cv will change from 3 to 5 in version 0.22. Specify it explicitly to silence this warning.
  warnings.warn(CV_WARNING, FutureWarning)
D:\Anaconda\lib\site-packages\sklearn\model_selection\_split.py:1978: FutureWarning: The default value of cv will change from 3 to 5 in version 0.22. Specify it explicitly to silence this warning.
  warnings.warn(CV_WARNING, FutureWarning)
D:\Anaconda\lib\site-packages\sklearn\model_selection\_split.py:1978: FutureWarning: The default value of cv will change from 3 to 5 in version 0.22. Specify it explicitly to silence this warning.
  warnings.warn(CV_WARNING, FutureWarning)
D:\Anaconda\lib\site-packages\sklearn\mo

fake run...


D:\Anaconda\lib\site-packages\sklearn\model_selection\_split.py:1978: FutureWarning: The default value of cv will change from 3 to 5 in version 0.22. Specify it explicitly to silence this warning.
  warnings.warn(CV_WARNING, FutureWarning)
D:\Anaconda\lib\site-packages\sklearn\model_selection\_split.py:1978: FutureWarning: The default value of cv will change from 3 to 5 in version 0.22. Specify it explicitly to silence this warning.
  warnings.warn(CV_WARNING, FutureWarning)
D:\Anaconda\lib\site-packages\sklearn\model_selection\_split.py:1978: FutureWarning: The default value of cv will change from 3 to 5 in version 0.22. Specify it explicitly to silence this warning.
  warnings.warn(CV_WARNING, FutureWarning)
D:\Anaconda\lib\site-packages\sklearn\model_selection\_split.py:1978: FutureWarning: The default value of cv will change from 3 to 5 in version 0.22. Specify it explicitly to silence this warning.
  warnings.warn(CV_WARNING, FutureWarning)
D:\Anaconda\lib\site-packages\sklearn\mo

In [ ]:
#1801
test_scores_by_labeling

In [31]:
#201
test_scores_by_labeling

{'real': {'accuracy': 0.8587786259541985,
  'balanced_accuracy': 0.8517857142857144,
  'precision': 0.8598726114649682,
  'recall': 0.9,
  'f1': 0.8794788273615636,
  'roc_auc': 0.9329761904761904},
 'fake': {'accuracy': 0.8587786259541985,
  'balanced_accuracy': 0.8517857142857144,
  'precision': 0.8571428571428571,
  'recall': 0.8035714285714286,
  'f1': 0.8294930875576038,
  'roc_auc': 0.9329761904761904}}

In [33]:
#1609
test_scores_by_labeling

{'real': {'accuracy': 0.851145038167939,
  'balanced_accuracy': 0.84625,
  'precision': 0.8627450980392157,
  'recall': 0.88,
  'f1': 0.8712871287128714,
  'roc_auc': 0.9041369047619048},
 'fake': {'accuracy': 0.851145038167939,
  'balanced_accuracy': 0.84625,
  'precision': 0.8348623853211009,
  'recall': 0.8125,
  'f1': 0.8235294117647057,
  'roc_auc': 0.9041369047619048}}

### ROC-curves 

In [36]:
from sklearn.pipeline import Pipeline

def end_to_end_roc(train_texts, train_labels_dict, test_texts, test_labels_dict, 
             ngram_feat_sets=[[[1]],[[0]],[[0]]], weight_schemes=['binary'], clfs=[clfLG]):  
    
    all_experiments = {}
    
    testing_score_stub = {'accuracy': -1, 
                           'balanced_accuracy': -1, 
                           'precision': -1, 
                           'recall': -1, 
                           'f1': -1, 
                           'roc_auc': -1}
    
    
    # for each combination of ngram feature types
    for i in range(len(ngram_feat_sets[0])):         
        cnvalues = ngram_feat_sets[0][i]
        wnvalues = ngram_feat_sets[1][i] 
        fnvalues = ngram_feat_sets[2][i] 
        ngram_feat_type_set_str = str(cnvalues[0]) +'-' + str(wnvalues[0]) + '-' + str(fnvalues[0]) + ' char-word-func'
        char_n_gram = cnvalues[0]
        word_n_gram = wnvalues[0]
        func_n_gram = fnvalues[0]
        
        feat_extractor = FeatureExtractor(cnvalues, wnvalues, fnvalues)        
        train_feature_mx, _ = feat_extractor.fit_extract(train_texts)
        test_feature_mx, _ = feat_extractor.extract(test_texts) 
        print('train shape: ', train_feature_mx.shape, 'test shape:', test_feature_mx.shape)
        
        #applying the frequency threshold
        cols_to_keep = apply_frequency_threshold(train_feature_mx)
        thresholded_train_feat_mx = train_feature_mx[:, cols_to_keep]
        thresholded_test_feat_mx = test_feature_mx[:, cols_to_keep]
        print('Thresholded train shape: ', thresholded_train_feat_mx.shape, 'test shape:', thresholded_test_feat_mx.shape)
        
        #for each weighting scheme, for each classifier, create a pipeline
        all_experiments[ngram_feat_type_set_str] = {}
        for weight_scheme_name in weight_schemes: 
            all_experiments[ngram_feat_type_set_str][weight_scheme_name] = {}
            weight_scheme = get_weighting_scheme(weight_scheme_name)
            for clf in clfs: 
                clf_name = type(clf).__name__
                print('Classifier: ' + clf_name)
                all_experiments[ngram_feat_type_set_str][weight_scheme_name][clf_name] = {}
                ppl = Pipeline([('scaler', weight_scheme), ('clf', clf)])

                test_scores_by_labeling = {}
                for key in train_labels_dict:
                    print(key + " run...")
                    train_X = thresholded_train_feat_mx.copy()
                    test_X = thresholded_test_feat_mx.copy() 

                    train_y = train_labels_dict[key]
                    test_y = test_labels_dict[key]                

                    print(thresholded_train_feat_mx.shape)
                    print("len train_y",  len(train_y))
                    # test run 
                    ppl.fit(train_X, train_y)
                    #acc, balanced_acc, p, r, f1, roc_auc
                    test_scores, y_pred_scores = check_model_fit(ppl, test_X, test_y)
                    print(test_scores)
                    test_scores_by_labeling[key] = y_pred_scores
                all_experiments[ngram_feat_type_set_str][weight_scheme_name][clf_name] = test_scores_by_labeling
    return all_experiments              

In [42]:
my_ngram_feat_combinations=[[[2]],[[0]],[[0]]]
my_weighting_schemes = ['norm', 'relat', 'none (tf)']
my_clfs = [clfAB]

ab_200 =end_to_end_roc(train_texts, train_labels_dict, test_texts, test_labels_dict, 
             my_ngram_feat_combinations, my_weighting_schemes, my_clfs)

Feature extractor for 2-0-0 char-word-func N-gram combination
train shape:  (638, 2029) test shape: (262, 2029)
Thresholded train shape:  (638, 1555) test shape: (262, 1555)
feature_weight = norm
Classifier: AdaBoostClassifier
real run...
fake run...
feature_weight = relat
Classifier: AdaBoostClassifier
real run...
fake run...
feature_weight = tf
Classifier: AdaBoostClassifier
real run...
fake run...


In [43]:
my_ngram_feat_combinations=[[[2]],[[0]],[[1]]]
my_weighting_schemes = ['norm', 'relat']
my_clfs = [clfAB]

ab_201 =end_to_end_roc(train_texts, train_labels_dict, test_texts, test_labels_dict, 
             my_ngram_feat_combinations, my_weighting_schemes, my_clfs)

Feature extractor for 2-0-1 char-word-func N-gram combination
train shape:  (638, 2339) test shape: (262, 2339)
Thresholded train shape:  (638, 1848) test shape: (262, 1848)
feature_weight = norm
Classifier: AdaBoostClassifier
real run...
fake run...
feature_weight = relat
Classifier: AdaBoostClassifier
real run...
fake run...


In [44]:
my_ngram_feat_combinations=[[[2]],[[1]],[[0]]]
my_weighting_schemes = ['binary']
my_clfs = [isotonic_svc]

ab_210 =end_to_end_roc(train_texts, train_labels_dict, test_texts, test_labels_dict, 
             my_ngram_feat_combinations, my_weighting_schemes, my_clfs)

Feature extractor for 2-1-0 char-word-func N-gram combination
train shape:  (638, 10376) test shape: (262, 10376)
Thresholded train shape:  (638, 5575) test shape: (262, 5575)
feature_weight = binary
Classifier: CalibratedClassifierCV
real run...
fake run...


/Users/alisa/workspace/Urdu_Fake_News/envname/lib/python3.7/site-packages/sklearn/model_selection/_split.py:2053: FutureWarning: You should specify a value for 'cv' instead of relying on the default value. The default value will change from 3 to 5 in version 0.22.
  warnings.warn(CV_WARNING, FutureWarning)
/Users/alisa/workspace/Urdu_Fake_News/envname/lib/python3.7/site-packages/sklearn/model_selection/_split.py:2053: FutureWarning: You should specify a value for 'cv' instead of relying on the default value. The default value will change from 3 to 5 in version 0.22.
  warnings.warn(CV_WARNING, FutureWarning)


In [ ]:
y_proba = {}
y_proba['test_y'] = list(test_labels_dict['fake'])
y_proba['1007'] = list(ab_200['2-0-0 char-word-func']['norm']['AdaBoostClassifier']['fake'][:, 1])
y_proba['1015'] = list(ab_200['2-0-0 char-word-func']['relat']['AdaBoostClassifier']['fake'][:, 1])
y_proba['1023'] = list(ab_200['2-0-0 char-word-func']['none (tf)']['AdaBoostClassifier']['fake'][:, 1])
y_proba['1967'] = list(ab_201['2-0-1 char-word-func']['norm']['AdaBoostClassifier']['fake'][:, 1])
y_proba['1975'] = list(ab_201['2-0-1 char-word-func']['relat']['AdaBoostClassifier']['fake'][:, 1])
y_proba['201'] = list(ab_210['2-1-0 char-word-func']['binary']['CalibratedClassifierCV']['fake'][:, 1])

import json 
json.dump(y_proba, open('results/y_probabilities_for_roccurve.json', 'w'))

In [34]:
my_ngram_feat_combinations=[[[1]],[[0]],[[1]]]
my_weighting_schemes = ['binary']
my_clfs = [clfAB]

ab_247 =end_to_end_roc(train_texts, train_labels_dict, test_texts, test_labels_dict, 
             my_ngram_feat_combinations, my_weighting_schemes, my_clfs)

Feature extractor for 1-0-1 char-word-func N-gram combination
train shape:  (638, 420) test shape: (262, 420)
Thresholded train shape:  (638, 394) test shape: (262, 394)
feature_weight = binary
Classifier: AdaBoostClassifier
real run...
(638, 394)
len train_y 638
{'accuracy': 0.8625954198473282, 'balanced_accuracy': 0.8551190476190476, 'precision': 0.8607594936708861, 'recall': 0.9066666666666666, 'f1': 0.8831168831168831, 'roc_auc': 0.9297916666666667}
fake run...
(638, 394)
len train_y 638
{'accuracy': 0.8625954198473282, 'balanced_accuracy': 0.8551190476190476, 'precision': 0.8653846153846154, 'recall': 0.8035714285714286, 'f1': 0.8333333333333334, 'roc_auc': 0.9297916666666668}


In [33]:
my_ngram_feat_combinations=[[[2]],[[2]],[[2]]]
my_weighting_schemes = ['binary']
my_clfs = [clfAB]

ab_159 =end_to_end_roc(train_texts, train_labels_dict, test_texts, test_labels_dict, 
             my_ngram_feat_combinations, my_weighting_schemes, my_clfs)

Feature extractor for 2-2-2 char-word-func N-gram combination
train shape:  (638, 40618) test shape: (262, 40618)
Thresholded train shape:  (638, 11448) test shape: (262, 11448)
feature_weight = binary
Classifier: AdaBoostClassifier
real run...
(638, 11448)
len train_y 638
{'accuracy': 0.8625954198473282, 'balanced_accuracy': 0.8483333333333334, 'precision': 0.8352941176470589, 'recall': 0.9466666666666667, 'f1': 0.8875, 'roc_auc': 0.9297619047619048}
fake run...
(638, 11448)
len train_y 638
{'accuracy': 0.8625954198473282, 'balanced_accuracy': 0.8483333333333334, 'precision': 0.9130434782608695, 'recall': 0.75, 'f1': 0.8235294117647057, 'roc_auc': 0.9297619047619049}


In [35]:
my_ngram_feat_combinations=[[[1]],[[1]],[[0]]]
my_weighting_schemes = ['logent']
my_clfs = [clfAB]

ab_775 =end_to_end_roc(train_texts, train_labels_dict, test_texts, test_labels_dict, 
             my_ngram_feat_combinations, my_weighting_schemes, my_clfs)

Feature extractor for 1-1-0 char-word-func N-gram combination
train shape:  (638, 8457) test shape: (262, 8457)
Thresholded train shape:  (638, 4121) test shape: (262, 4121)
feature_weight = logent
Classifier: AdaBoostClassifier
real run...
(638, 4121)
len train_y 638
{'accuracy': 0.8664122137404581, 'balanced_accuracy': 0.8629761904761906, 'precision': 0.8807947019867549, 'recall': 0.8866666666666667, 'f1': 0.8837209302325582, 'roc_auc': 0.9412797619047619}
fake run...
(638, 4121)
len train_y 638
{'accuracy': 0.8664122137404581, 'balanced_accuracy': 0.8629761904761906, 'precision': 0.8468468468468469, 'recall': 0.8392857142857143, 'f1': 0.8430493273542602, 'roc_auc': 0.9412797619047619}


In [36]:
my_ngram_feat_combinations=[[[3]],[[1]],[[0]]]
my_weighting_schemes = ['norm']
my_clfs = [isotonic_svc]

ab_1801 =end_to_end_roc(train_texts, train_labels_dict, test_texts, test_labels_dict, 
             my_ngram_feat_combinations, my_weighting_schemes, my_clfs)

Feature extractor for 3-1-0 char-word-func N-gram combination
train shape:  (638, 20013) test shape: (262, 20013)
Thresholded train shape:  (638, 11947) test shape: (262, 11947)
feature_weight = norm
Classifier: CalibratedClassifierCV
real run...
(638, 11947)
len train_y 638
{'accuracy': 0.8435114503816794, 'balanced_accuracy': 0.8316666666666667, 'precision': 0.8303030303030303, 'recall': 0.9133333333333333, 'f1': 0.8698412698412699, 'roc_auc': 0.9135416666666667}
fake run...
(638, 11947)
len train_y 638


/Users/alisa/workspace/Urdu_Fake_News/envname/lib/python3.7/site-packages/sklearn/model_selection/_split.py:2053: FutureWarning: You should specify a value for 'cv' instead of relying on the default value. The default value will change from 3 to 5 in version 0.22.
  warnings.warn(CV_WARNING, FutureWarning)
/Users/alisa/workspace/Urdu_Fake_News/envname/lib/python3.7/site-packages/sklearn/model_selection/_split.py:2053: FutureWarning: You should specify a value for 'cv' instead of relying on the default value. The default value will change from 3 to 5 in version 0.22.
  warnings.warn(CV_WARNING, FutureWarning)


{'accuracy': 0.8435114503816794, 'balanced_accuracy': 0.8316666666666667, 'precision': 0.865979381443299, 'recall': 0.75, 'f1': 0.8038277511961722, 'roc_auc': 0.9135416666666667}


In [38]:
import json 
y_proba = json.load(open('results/y_probabilities_for_roccurve.json'))
y_proba.keys()

dict_keys(['test_y', '1007', '1015', '1023', '1967', '1975', '201'])

In [40]:
y_proba['159'] = list(ab_159['2-2-2 char-word-func']['binary']['AdaBoostClassifier']['fake'][:, 1])
y_proba['775'] = list(ab_775['1-1-0 char-word-func']['logent']['AdaBoostClassifier']['fake'][:, 1])
y_proba['247'] = list(ab_247['1-0-1 char-word-func']['binary']['AdaBoostClassifier']['fake'][:, 1])
y_proba['1801'] = list(ab_1801['3-1-0 char-word-func']['norm']['CalibratedClassifierCV']['fake'][:, 1])
y_proba.keys()

dict_keys(['test_y', '1007', '1015', '1023', '1967', '1975', '201', '159', '775', '247', '1801'])

In [41]:
# storing the results for analysis
import json 
json.dump(y_proba, open('results/y_probabilities_for_roccurve.json', 'w'))

## Exp for EMNLP

##### Corpsus Machine Translation :

In [43]:
#For EMNLP paper: 

my_ngram_feat_combinations=[[[2]],[[0]],[[0]]]
my_weighting_schemes = ['norm', 'relat', 'none (tf)']
my_clfs = [clfAB]

ab_200 =end_to_end_roc(train_texts, train_labels_dict, test_texts, test_labels_dict, 
             my_ngram_feat_combinations, my_weighting_schemes, my_clfs)

Feature extractor for 2-0-0 char-word-func N-gram combination
train shape:  (280, 1398) test shape: (120, 1398)
Thresholded train shape:  (280, 1092) test shape: (120, 1092)
feature_weight = norm
Classifier: AdaBoostClassifier
real run...
(280, 1092)
len train_y 280
{'accuracy': 0.83333333333333337, 'balanced_accuracy': 0.83333333333333326, 'precision': 0.84482758620689657, 'recall': 0.81666666666666665, 'f1': 0.83050847457627119, 'roc_auc': 0.91416666666666657}
fake run...
(280, 1092)
len train_y 280
{'accuracy': 0.83333333333333337, 'balanced_accuracy': 0.83333333333333326, 'precision': 0.82258064516129037, 'recall': 0.84999999999999998, 'f1': 0.83606557377049184, 'roc_auc': 0.91416666666666657}
feature_weight = relat
Classifier: AdaBoostClassifier
real run...
(280, 1092)
len train_y 280
{'accuracy': 0.83333333333333337, 'balanced_accuracy': 0.83333333333333326, 'precision': 0.84482758620689657, 'recall': 0.81666666666666665, 'f1': 0.83050847457627119, 'roc_auc': 0.91416666666666657}

In [44]:
my_ngram_feat_combinations=[[[2]],[[0]],[[1]]]
my_weighting_schemes = ['norm', 'relat']
my_clfs = [clfAB]

ab_201 =end_to_end_roc(train_texts, train_labels_dict, test_texts, test_labels_dict, 
             my_ngram_feat_combinations, my_weighting_schemes, my_clfs)

Feature extractor for 2-0-1 char-word-func N-gram combination
train shape:  (280, 1663) test shape: (120, 1663)
Thresholded train shape:  (280, 1314) test shape: (120, 1314)
feature_weight = norm
Classifier: AdaBoostClassifier
real run...
(280, 1314)
len train_y 280
{'accuracy': 0.80833333333333335, 'balanced_accuracy': 0.80833333333333335, 'precision': 0.83636363636363631, 'recall': 0.76666666666666672, 'f1': 0.80000000000000004, 'roc_auc': 0.91555555555555546}
fake run...
(280, 1314)
len train_y 280
{'accuracy': 0.80833333333333335, 'balanced_accuracy': 0.80833333333333335, 'precision': 0.7846153846153846, 'recall': 0.84999999999999998, 'f1': 0.81599999999999995, 'roc_auc': 0.91555555555555546}
feature_weight = relat
Classifier: AdaBoostClassifier
real run...
(280, 1314)
len train_y 280
{'accuracy': 0.80833333333333335, 'balanced_accuracy': 0.80833333333333335, 'precision': 0.83636363636363631, 'recall': 0.76666666666666672, 'f1': 0.80000000000000004, 'roc_auc': 0.91555555555555546}


In [45]:
my_ngram_feat_combinations=[[[2]],[[1]],[[0]]]
my_weighting_schemes = ['binary']
my_clfs = [isotonic_svc]

ab_210 =end_to_end_roc(train_texts, train_labels_dict, test_texts, test_labels_dict, 
             my_ngram_feat_combinations, my_weighting_schemes, my_clfs)

Feature extractor for 2-1-0 char-word-func N-gram combination
train shape:  (280, 4401) test shape: (120, 4401)
Thresholded train shape:  (280, 2492) test shape: (120, 2492)
feature_weight = binary
Classifier: CalibratedClassifierCV
real run...
(280, 2492)
len train_y 280
{'accuracy': 0.77500000000000002, 'balanced_accuracy': 0.77499999999999991, 'precision': 0.80000000000000004, 'recall': 0.73333333333333328, 'f1': 0.76521739130434785, 'roc_auc': 0.83347222222222217}
fake run...
(280, 2492)
len train_y 280
{'accuracy': 0.77500000000000002, 'balanced_accuracy': 0.77499999999999991, 'precision': 0.75384615384615383, 'recall': 0.81666666666666665, 'f1': 0.78400000000000003, 'roc_auc': 0.83347222222222228}


D:\Anaconda\lib\site-packages\sklearn\model_selection\_split.py:1978: FutureWarning: The default value of cv will change from 3 to 5 in version 0.22. Specify it explicitly to silence this warning.
  warnings.warn(CV_WARNING, FutureWarning)
D:\Anaconda\lib\site-packages\sklearn\model_selection\_split.py:1978: FutureWarning: The default value of cv will change from 3 to 5 in version 0.22. Specify it explicitly to silence this warning.
  warnings.warn(CV_WARNING, FutureWarning)


In [47]:
my_ngram_feat_combinations=[[[1]],[[0]],[[1]]]
my_weighting_schemes = ['binary']
my_clfs = [clfAB]

ab_247 =end_to_end_roc(train_texts, train_labels_dict, test_texts, test_labels_dict, 
             my_ngram_feat_combinations, my_weighting_schemes, my_clfs)

Feature extractor for 1-0-1 char-word-func N-gram combination
train shape:  (280, 357) test shape: (120, 357)
Thresholded train shape:  (280, 308) test shape: (120, 308)
feature_weight = binary
Classifier: AdaBoostClassifier
real run...
(280, 308)
len train_y 280
{'accuracy': 0.64166666666666672, 'balanced_accuracy': 0.64166666666666661, 'precision': 0.65454545454545454, 'recall': 0.59999999999999998, 'f1': 0.62608695652173918, 'roc_auc': 0.71666666666666667}
fake run...
(280, 308)
len train_y 280
{'accuracy': 0.64166666666666672, 'balanced_accuracy': 0.64166666666666661, 'precision': 0.63076923076923075, 'recall': 0.68333333333333335, 'f1': 0.65599999999999992, 'roc_auc': 0.71666666666666667}


In [48]:
my_ngram_feat_combinations=[[[2]],[[2]],[[2]]]
my_weighting_schemes = ['binary']
my_clfs = [clfAB]

ab_159 =end_to_end_roc(train_texts, train_labels_dict, test_texts, test_labels_dict, 
             my_ngram_feat_combinations, my_weighting_schemes, my_clfs)

Feature extractor for 2-2-2 char-word-func N-gram combination
train shape:  (280, 9110) test shape: (120, 9110)
Thresholded train shape:  (280, 3073) test shape: (120, 3073)
feature_weight = binary
Classifier: AdaBoostClassifier
real run...
(280, 3073)
len train_y 280
{'accuracy': 0.78333333333333333, 'balanced_accuracy': 0.78333333333333333, 'precision': 0.82692307692307687, 'recall': 0.71666666666666667, 'f1': 0.7678571428571429, 'roc_auc': 0.87611111111111106}
fake run...
(280, 3073)
len train_y 280
{'accuracy': 0.78333333333333333, 'balanced_accuracy': 0.78333333333333333, 'precision': 0.75, 'recall': 0.84999999999999998, 'f1': 0.79687499999999989, 'roc_auc': 0.87611111111111106}


In [49]:
my_ngram_feat_combinations=[[[1]],[[1]],[[0]]]
my_weighting_schemes = ['logent']
my_clfs = [clfAB]

ab_775 =end_to_end_roc(train_texts, train_labels_dict, test_texts, test_labels_dict, 
             my_ngram_feat_combinations, my_weighting_schemes, my_clfs)

Feature extractor for 1-1-0 char-word-func N-gram combination
train shape:  (280, 3095) test shape: (120, 3095)
Thresholded train shape:  (280, 1486) test shape: (120, 1486)
feature_weight = logent
Classifier: AdaBoostClassifier
real run...
(280, 1486)
len train_y 280
{'accuracy': 0.69166666666666665, 'balanced_accuracy': 0.69166666666666665, 'precision': 0.65753424657534243, 'recall': 0.80000000000000004, 'f1': 0.72180451127819545, 'roc_auc': 0.70416666666666672}
fake run...
(280, 1486)
len train_y 280
{'accuracy': 0.69166666666666665, 'balanced_accuracy': 0.69166666666666665, 'precision': 0.74468085106382975, 'recall': 0.58333333333333337, 'f1': 0.65420560747663548, 'roc_auc': 0.70416666666666672}


In [50]:
my_ngram_feat_combinations=[[[3]],[[1]],[[0]]]
my_weighting_schemes = ['norm']
my_clfs = [isotonic_svc]

ab_1801 =end_to_end_roc(train_texts, train_labels_dict, test_texts, test_labels_dict, 
             my_ngram_feat_combinations, my_weighting_schemes, my_clfs)

Feature extractor for 3-1-0 char-word-func N-gram combination
train shape:  (280, 9518) test shape: (120, 9518)
Thresholded train shape:  (280, 5661) test shape: (120, 5661)
feature_weight = norm
Classifier: CalibratedClassifierCV
real run...
(280, 5661)
len train_y 280
{'accuracy': 0.67500000000000004, 'balanced_accuracy': 0.67500000000000004, 'precision': 0.66153846153846152, 'recall': 0.71666666666666667, 'f1': 0.68799999999999994, 'roc_auc': 0.76791666666666669}
fake run...
(280, 5661)
len train_y 280
{'accuracy': 0.67500000000000004, 'balanced_accuracy': 0.67500000000000004, 'precision': 0.69090909090909092, 'recall': 0.6333333333333333, 'f1': 0.66086956521739126, 'roc_auc': 0.76791666666666669}


D:\Anaconda\lib\site-packages\sklearn\model_selection\_split.py:1978: FutureWarning: The default value of cv will change from 3 to 5 in version 0.22. Specify it explicitly to silence this warning.
  warnings.warn(CV_WARNING, FutureWarning)
D:\Anaconda\lib\site-packages\sklearn\model_selection\_split.py:1978: FutureWarning: The default value of cv will change from 3 to 5 in version 0.22. Specify it explicitly to silence this warning.
  warnings.warn(CV_WARNING, FutureWarning)


In [51]:
y_proba['159'] = list(ab_159['2-2-2 char-word-func']['binary']['AdaBoostClassifier']['fake'][:, 1])
y_proba['775'] = list(ab_775['1-1-0 char-word-func']['logent']['AdaBoostClassifier']['fake'][:, 1])
y_proba['247'] = list(ab_247['1-0-1 char-word-func']['binary']['AdaBoostClassifier']['fake'][:, 1])
y_proba['1801'] = list(ab_1801['3-1-0 char-word-func']['norm']['CalibratedClassifierCV']['fake'][:, 1])
y_proba.keys()

dict_keys(['test_y', '1007', '1015', '1023', '1967', '1975', '201', '159', '775', '247', '1801'])

In [52]:
y_proba = {}
y_proba['test_y'] = list(test_labels_dict['fake'])
y_proba['1007'] = list(ab_200['2-0-0 char-word-func']['norm']['AdaBoostClassifier']['fake'][:, 1])
y_proba['1015'] = list(ab_200['2-0-0 char-word-func']['relat']['AdaBoostClassifier']['fake'][:, 1])
y_proba['1023'] = list(ab_200['2-0-0 char-word-func']['none (tf)']['AdaBoostClassifier']['fake'][:, 1])
y_proba['1967'] = list(ab_201['2-0-1 char-word-func']['norm']['AdaBoostClassifier']['fake'][:, 1])
y_proba['1975'] = list(ab_201['2-0-1 char-word-func']['relat']['AdaBoostClassifier']['fake'][:, 1])
y_proba['201'] = list(ab_210['2-1-0 char-word-func']['binary']['CalibratedClassifierCV']['fake'][:, 1])

y_proba['159'] = list(ab_159['2-2-2 char-word-func']['binary']['AdaBoostClassifier']['fake'][:, 1])
y_proba['775'] = list(ab_775['1-1-0 char-word-func']['logent']['AdaBoostClassifier']['fake'][:, 1])
y_proba['247'] = list(ab_247['1-0-1 char-word-func']['binary']['AdaBoostClassifier']['fake'][:, 1])
y_proba['1801'] = list(ab_1801['3-1-0 char-word-func']['norm']['CalibratedClassifierCV']['fake'][:, 1])
y_proba.keys()


import json 
json.dump(y_proba, open('results/y_probabilities_for_roccurve_MT.json', 'w'))